In [1]:
# @title Python modulok betoltese es beallitasa

# nem kellenek programozasi figyelmeztetesek
import warnings
warnings.filterwarnings('ignore')

# matrixmuveletek
import pandas as pd
pd.set_option('display.precision', 2)

# matematikai modul
import numpy as np
import base64

# statisztikai modul
from scipy.spatial import distance_matrix

#infografika
import plotly.express as px

from math import cos, sin, atan2, sqrt, pi, acos, asin


In [2]:
# @title BKK adatok betoltese
# @markdown **A BKK egy meglepoen magas szinvonalu intezmenynek tunik.** Az utvonal,<br>
# @markdown amerre a jaratok jarnak, meterre pontosan elerheto, jaratidokkel,<br>
# @markdown megallok koordinataival, adataival egyutt, iparagi szabvany szerint <br>
# @markdown strukturalva, par naponta frissitve. Az pedig, hogy az egyes jaratok<br>
# @markdown eppen hol vannak, milyen elakadasok vannak, mi a varhato valos<br>
# @markdown erkezes, szinten ingyen, elo adatkapcsolatban elerheto. Szep munka.

src_path = './data/'

routes = pd.read_csv(src_path + 'routes.txt', encoding='utf-8',
                     usecols=[1,2,4,5])

stops = pd.read_csv(src_path + 'stops.txt', encoding='utf-8')

stop_times = pd.read_csv(src_path + 'stop_times.txt', usecols=[0,1,2,3,4,5,8],
                         encoding='utf-8', dtype='str',
                         converters={'shape_dist_traveled':float,
                                     'stop_sequence':int})

trips = pd.read_csv(src_path + 'trips.txt',
                    dtype='str', converters={'direction_id':int})

In [3]:
# @title folosleges adatok eldobalasa, adatformazas
# @markdown ### A kovetkezo adatokat tartottuk meg:<br>
# @markdown - **Megallok:** megallokod, nev, koordinatak
# @markdown - **Indulasok:** jaratkod, megallokod, megallo sorszama, erkezesi ido
# @markdown - **Jaratok:** jarmuazonosito, utvonalkod, utvonalkod, utvonalnev, iranykod
# @markdown - **Utvonalak:** utvonalkod, utvonalnev, jarmutipus, utvonal neve<br><br>
# @markdown Eldobtam a hajojaratokat, futunk a villamos utan, nem uszunk.

stops = stops[['stop_id','stop_name','stop_lat','stop_lon']] #6.1k records
stop_times = stop_times[['trip_id','stop_id','stop_sequence','arrival_time', 'departure_time']] #4.6M records
trips = trips[['service_id','route_id','trip_id','trip_headsign','direction_id']] #228k records

This may take a while (like a full minute or so), but we need it.

In [4]:
# erkezesi ido: szovegbol idopontta konverzio
stop_times.arrival_time = stop_times.arrival_time.apply(pd.to_timedelta)
stop_times.departure_time = stop_times.departure_time.apply(pd.to_timedelta)

### Reducing the amount of data, out of an unwillingness to swim
For now we have a bunch of data, namely:

In [5]:
print(f"{len(routes)} routes, {len(trips)} trips, {len(stops)} stops, and finally {len(stop_times)} times a vehicle has stopped at a stop.")

374 routes, 228377 trips, 6149 stops, and finally 4656177 times a vehicle has stopped at a stop.


To reduce this we simply drop all the ferry trips.

In [6]:
# not running after ferries
routes = routes[routes.route_type != 4]

#but then we can drop a bunch of ferry trips too, cant't we?
trips = trips[trips['route_id'].isin(routes.set_index('route_id').index)].reset_index().drop('index', axis = 1) #why can't I just use the 'in' operator???

#nor do we have to consider the stops made in these trips, wuhuuu
stop_times = stop_times[stop_times.trip_id.isin(trips.set_index('trip_id').index)].reset_index().drop('index', axis = 1)

So now we end up with slightly less data, namely:

In [7]:
print(f"{len(routes)} routes, {len(trips)} trips, {len(stops)} stops, and finally {len(stop_times)} times a vehicle has stopped at a stop.")

373 routes, 228271 trips, 6149 stops, and finally 4655965 times a vehicle has stopped at a stop.


Okay, maybe this didn['t get rid of that much data, but it sure has gotten rid of the most annoying part]

## Intermezzo: deciding the amount of stops we want to run
For now I will just set this to be from 1 to 5, but this is where it can be changed.

In [8]:
RUN_DISTANCE_IN_STOPS = [1, 2, 3, 4, 5]

## Creating a list of stop pairs that are *adjacent* on the same route
We can already get some of the important data:
- **from_id**: the first stop in the pair
- **to_id**: the second stop of the pair
- **route_id**: the route on which these stops are adjecent

But the really juicy parts that we are after will take a bit more time to obtain, so we will not add the following columons yet:
- **total_travel_time**: the total time that was spent travelling this section
- **data_count**: the number of times this section was travelled
- **average_time**: we need this to know if we could outrun te tram on a normal day
- **fastest_time**: likely not that interesting, but his is what we must beat to always be able to outrun it
- **slowest_time**: a bit more interesting, if we can't even beat this, we coul neve hope to win

In [9]:
#we don't have the next stop, or the route id in the stops df, so we start with this
temp_stop_pairs = stop_times[['trip_id', 'stop_id', 'stop_sequence']]

#get the route id from the trip id
temp_stop_pairs['route_id'] = trips.set_index('trip_id')['route_id'].loc[temp_stop_pairs.trip_id].reset_index()['route_id'] #some crazy shit to make pyhton not complain
#if we want the headsign later, we need to get it now, while we have the trip_id
temp_stop_pairs['trip_headsign'] = trips.set_index('trip_id')['trip_headsign'].loc[temp_stop_pairs.trip_id].reset_index()['trip_headsign'] #some crazy shit to make pyhton not complain

#now we also wanto to get the next stop if there is one, or drop the row if there isn't, this will effectively give us the pairs we wanted
#furthermore we want to do this for every distance that we are interested in
stop_pairs = None
for stop_distance in RUN_DISTANCE_IN_STOPS:
    adding_stop_pairs = temp_stop_pairs
    adding_stop_pairs['to_id'] = temp_stop_pairs.groupby('trip_id').shift(-stop_distance)['stop_id']
    adding_stop_pairs['stop_count'] = stop_distance
    adding_stop_pairs = adding_stop_pairs.dropna()

    if stop_pairs is None:
        stop_pairs = adding_stop_pairs
    else:
        stop_pairs = pd.concat([stop_pairs, adding_stop_pairs])


#now we can finally get rid of the two extra columns, and since we will end up with a number of duplicates, we can also drop those
stop_pairs = stop_pairs[['route_id', 'stop_id', 'to_id', 'stop_count', 'trip_headsign']].rename(columns={'stop_id':'from_id'}).drop_duplicates()
stop_pairs = stop_pairs.reset_index()[['route_id', 'from_id', 'to_id', 'stop_count', 'trip_headsign']] #shenanigans needed to get the index  right
stop_pairs

route_id   from_id     to_id  stop_count trip_headsign
0         3480    007884    F01012           1   Savoya Park
1         3480    F01012    F01005           1   Savoya Park
2         3480    F01005    F00921           1   Savoya Park
3         3480    F00921    008590           1   Savoya Park
4         3480    008590    F02148           1   Savoya Park
...        ...       ...       ...         ...           ...
95127       H5  09068196  09175206           5   Békásmegyer
95128       H5  09118198  09183208           5   Békásmegyer
95129       H5  09001188  09118198           5   Békásmegyer
95130       H5  09001187  09118198           5   Békásmegyer
95131       H5  09118198  09183209           5   Békásmegyer

[95132 rows x 5 columns]

### To get the total travel time, we need to figure out the travel time for each stop
Lets start by getting the info of the next stop in the stop_times frame, we can use this later to calculate deltas.

In [10]:
temp_new_stop_times = stop_times.drop('stop_sequence', axis=1) #we won't need the sequence numbers

new_stop_times = None
for stop_distance in RUN_DISTANCE_IN_STOPS:
    adding_new_stop_times = temp_new_stop_times
    adding_new_stop_times[['next_stop_id', 'next_arrival_time', 'next_departure_time']] = temp_new_stop_times.groupby('trip_id').shift(-stop_distance)[['stop_id', 'arrival_time', 'departure_time']] #get the next values
    adding_new_stop_times['stop_count'] = stop_distance
    adding_new_stop_times = adding_new_stop_times.dropna()

    if new_stop_times is None:
        new_stop_times = adding_new_stop_times
    else:
        new_stop_times = pd.concat([new_stop_times, adding_new_stop_times])

new_stop_times = new_stop_times.dropna().reset_index().drop('index', axis=1) #don't need the finals stops, also fix the index
new_stop_times

trip_id   stop_id    arrival_time  departure_time next_stop_id  \
0         C11388145    007884 0 days 08:46:00 0 days 08:46:00       F01012   
1         C11388145    F01012 0 days 08:47:00 0 days 08:47:00       F01005   
2         C11388145    F01005 0 days 08:49:00 0 days 08:49:00       F00921   
3         C11388145    F00921 0 days 08:50:00 0 days 08:50:00       008590   
4         C11388145    008590 0 days 08:53:00 0 days 08:53:00       F02148   
...             ...       ...             ...             ...          ...   
19863852    H8000_1  09100202 1 days 00:35:00 1 days 00:35:00     09191212   
19863853    H8000_1  09159204 1 days 00:37:00 1 days 00:37:00     09209214   
19863854    H8000_1  09175206 1 days 00:39:00 1 days 00:39:00     09134218   
19863855    H8000_1  09183208 1 days 00:42:00 1 days 00:43:00     09217219   
19863856    H8000_1  09126211 1 days 00:46:00 1 days 00:46:00     09142223   

         next_arrival_time next_departure_time  stop_count  
0          0 days 08:47:00     0 days 08:47:00           1  
1          0 days 08:49:00     0 days 08:49:00           1  
2          0 days 08:50:00     0 days 08:50:00           1  
3          0 days 08:53:00     0 days 08:53:00           1  
4          0 days 08:55:00     0 days 08:55:00           1  
...                    ...                 ...         ...  
19863852   1 days 00:48:00     1 days 00:48:00           5  
19863853   1 days 00:50:00     1 days 00:50:00           5  
19863854   1 days 00:52:00     1 days 00:53:00           5  
19863855   1 days 00:57:00     1 days 00:57:00           5  
19863856   1 days 01:00:00     1 days 01:00:00           5  

[19863857 rows x 8 columns]

Now we can calculate the delta for each stop, but there are many options we can explore, namely:
- arrival-arrival
- arrival-departure
- departure-arrival
- departure-departure

I will choose the **departure-arrival** option, as while this may be the strictest (including only the travel time of the vehicle), as this is the most impressive feat indeed, and this is needd for the full trick to work.

In [11]:
new_stop_times['travel_time'] = new_stop_times['next_arrival_time'] - new_stop_times['departure_time'] #calculating the delta

With this done we can get the route_id for each stop pair (so we can add them to the previously constructed dataframe), and then we can clean up the extra columns, fortunatley both are quite easy at this point based on previous work.

In [12]:
new_stop_times['route_id'] = trips.set_index('trip_id')['route_id'].loc[new_stop_times.trip_id].reset_index()['route_id'] #we did this before
new_stop_times = new_stop_times.drop(['trip_id', 'arrival_time', 'departure_time', 'next_arrival_time', 'next_departure_time'], axis = 1) #dropping the extra data

In [13]:
new_stop_times

stop_id next_stop_id  stop_count     travel_time route_id
0           007884       F01012           1 0 days 00:01:00     3480
1           F01012       F01005           1 0 days 00:02:00     3480
2           F01005       F00921           1 0 days 00:01:00     3480
3           F00921       008590           1 0 days 00:03:00     3480
4           008590       F02148           1 0 days 00:02:00     3480
...            ...          ...         ...             ...      ...
19863852  09100202     09191212           5 0 days 00:13:00       H5
19863853  09159204     09209214           5 0 days 00:13:00       H5
19863854  09175206     09134218           5 0 days 00:13:00       H5
19863855  09183208     09217219           5 0 days 00:14:00       H5
19863856  09126211     09142223           5 0 days 00:14:00       H5

[19863857 rows x 5 columns]

### Intermezzo: Did we time travel at any point?
Lets count the cases where the travel time was, less than 0 (and we might as well count the teleportations too, though these are not invalid events, just inaccurate measurements)!

In [14]:
time_travel_count = len(new_stop_times[new_stop_times.travel_time < pd.to_timedelta('0:00:00')])
teleportation_count = len(new_stop_times[new_stop_times.travel_time == pd.to_timedelta('0:00:00')])
total_trips = len(new_stop_times)
print(f"The number of time travels is: {time_travel_count}, accounting for {(time_travel_count / total_trips * 100):.2f}% of the data.")
print(f"The number of teleportations is: {teleportation_count}, accounting for {(teleportation_count / total_trips * 100):.2f}% of the data.")

The number of time travels is: 0, accounting for 0.00% of the data.
The number of teleportations is: 281188, accounting for 1.42% of the data.


### Aggregating all the data
Now that we have each travel time calculated we can easily aggregate this data, getting all the interesting columns for our stop pairs.

In [15]:
stop_pairs['total_travel_time'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].sum().reset_index()['travel_time'] #there HAS to be a better way
stop_pairs['mean_travel_time'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].mean().reset_index()['travel_time'] #there HAS to be a better way
stop_pairs['max_travel_time'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].max().reset_index()['travel_time'] #there HAS to be a better way
stop_pairs['min_travel_time'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].min().reset_index()['travel_time'] #there HAS to be a better way
stop_pairs['median_travel_time'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].median().reset_index()['travel_time'] #there HAS to be a better way
stop_pairs['travel_count'] = new_stop_times.groupby(['route_id', 'stop_id', 'next_stop_id', 'stop_count'])['travel_time'].count().reset_index()['travel_time'] #there HAS to be a better way

## Final touches
To find out whether we can run faster than public transit we still need to know its speed, and for that we need to know the distance between each pair of stops. So lets calculate these values now, starting with distance!

In [16]:
#first we get the latitudes and longitudes of the stops, we can drop these later
stop_pairs['from_lat'] = stops.set_index('stop_id').stop_lat.loc[stop_pairs.from_id].reset_index().stop_lat #boy do I loooove python
stop_pairs['from_lon'] = stops.set_index('stop_id').stop_lon.loc[stop_pairs.from_id].reset_index().stop_lon 
stop_pairs['to_lat'] = stops.set_index('stop_id').stop_lat.loc[stop_pairs.to_id].reset_index().stop_lat 
stop_pairs['to_lon'] = stops.set_index('stop_id').stop_lon.loc[stop_pairs.to_id].reset_index().stop_lon

#lets define the function to calculate the distance from lat and lon
def getDistanceFromLatLonInKmFastVersion(lat1, lon1, lat2, lon2):
    r = 6371 # km
    p = pi / 180

    a = 0.5 - cos((lat2-lat1)*p)/2 + cos(lat1*p) * cos(lat2*p) * (1-cos((lon2-lon1)*p))/2
    return 2 * r * asin(sqrt(a))

def getDistanceFromLatLonInKm(lat1,lon1,lat2,lon2):
    r = 6371; # Radius of the earth in km
    dLat = deg2rad(lat2-lat1)  # deg2rad below
    dLon = deg2rad(lon2-lon1) 
    a = np.sin(dLat/2) * np.sin(dLat/2) + cos(deg2rad(lat1)) * cos(deg2rad(lat2)) * sin(dLon/2) * sin(dLon/2) 
    c = 2 * atan2(sqrt(a), sqrt(1-a))
    d = r * c; # Distance in km
    return d

def deg2rad(deg):
  return deg * (pi/180)

def distance(lat1, lon1, lat2, lon2): #NOTHING WORKS GAAAAH
   return acos(sin(lat1)*sin(lat2)+cos(lat1)*cos(lat2)*cos(lon2-lon1))*6371

#with this info in hand we can do some math wizardry assuming the earth to be a perfect sphere, to get the distances of our stop pairs (in km)
stop_pairs['distance'] = stop_pairs.apply(lambda r: getDistanceFromLatLonInKm(r.from_lat, r.from_lon, r.to_lat, r.to_lon), axis=1)

#now we can just drop the superflous columns
stop_pairs = stop_pairs.drop(['from_lat', 'from_lon', 'to_lat', 'to_lon'], axis=1)

Before we can calculate speed we need to take care of one final task: we will need to deal those cases where the travel time was always less then a minute, as we can't calculate a speed for this.
For now I will just drop these rows, but we could for example set them to be the minimum valid time.

In [17]:
dropped = len(stop_pairs[~(stop_pairs.max_travel_time > pd.to_timedelta('0:00:00'))])
total = len(stop_pairs)
print(f"number of rows dropped is:{dropped}, or about {((dropped / total) * 100):.2f}% of the data.")
stop_pairs = stop_pairs[stop_pairs.max_travel_time > pd.to_timedelta('0:00:00')]

number of rows dropped is:21555, or about 22.66% of the data.


Now we can finally calculate the speed, I will use the mean travel time to do this, but all the others could be used too.

In [18]:
def get_speed(time:pd.Timedelta, distance:float):
    #distance is already in kilometers, great!
    #so we just need to convert the timedelta into hours
    hours = time / pd.Timedelta('1 hour')
    return distance / hours #km/h

stop_pairs['speed'] = stop_pairs.apply(lambda r: get_speed(r.mean_travel_time, r.distance), axis=1)

## Now we need to clean the data, and add all the interesting infos in
Lets start by getting rid of the clearly irrelevant rows:
- we won't run faster than 20 km/h, we are only human after all
- we won't run farther than 2km, we may be fit, but not *that* fit

In [19]:
stop_pairs = stop_pairs[stop_pairs.speed <= 20]
stop_pairs = stop_pairs[stop_pairs.distance <= 2]

### Now we want to expand the route_id and stop_id fields to be meaningful to the *lowly humans* reading it.
First is adding the route info.

In [20]:
stop_pairs[['route_short_name', 'route_type', 'route_desc']] = routes.set_index('route_id').loc[stop_pairs.route_id].reset_index()[['route_short_name', 'route_type', 'route_desc']]
# renaming route type codes with descriptions
typedict = {
    0:'tram',
    1:'metro',
    3:'bus',
    11:'troli',
    109: 'HEV'
}
stop_pairs.route_type.replace(typedict, inplace=True)

Second are the details of the trip, namely the headsign:

In [21]:
#heyyyy we already did this a while ago :)

And finally the details of the two stops:

In [22]:
stop_pairs['from_stop_name'] = stops.set_index('stop_id')['stop_name'].loc[stop_pairs.from_id].reset_index()['stop_name']
stop_pairs['to_stop_name'] = stops.set_index('stop_id')['stop_name'].loc[stop_pairs.to_id].reset_index()['stop_name']

## Time for the shinies!!!

### And we also should add some nice infos while we are at it.

In [23]:
stop_pairs['route_info'] = (
    stop_pairs.route_type.str.upper() + ' ' +
    stop_pairs.route_short_name + ' (in the direction of ' +
    stop_pairs.trip_headsign + ')')
stop_pairs['run_info'] = (
    stop_pairs.from_stop_name + ' >> ' +
    stop_pairs.to_stop_name + ' (' +
    stop_pairs.stop_count.astype(str) + ' stops)'
)
stop_pairs['time_info'] = (
    stop_pairs.distance.round(2).astype(str) + ' kilometers in ' +
    stop_pairs.mean_travel_time.astype('timedelta64[s]').astype(str) + ' (' +
    stop_pairs.speed.round(2).astype(str) + ' km/h speed)'
)

In [24]:
fig = px.scatter(
    stop_pairs,
    x="distance",
    y="speed",

    size='stop_count',
    opacity=.2,
    width=1000,
    height=800,

    color="route_type",
    color_discrete_map={'bus':'blue','tram':'goldenrod','troli':'red','metro':'black', 'HEV':'green'},
    custom_data=['route_info','run_info','time_info'],

    title="""<b>Hogyan fussunk gyorsabban, mint a villamos? *
             </b></br></br>* <i>képességeinkhez választva a kihívást</i>""",
    labels={
      "distance": "Távolság (km)",
      "speed": "Sebesség (km/h)",
      "route_type": "Jármű típusa",
      "mean_travel_time": "Futás ideje (sec)"
    }
)

fig.update_layout(
    hoverlabel=dict(
        bgcolor="white",
        font_size=16,
        font_family="Rockwell"
    ),
    legend=dict(
        yanchor="bottom",
        y=0.10,
        xanchor="right",
        x=0.90,
        font = dict(size = 16)
    )
)

fig.update_traces(
    hovertemplate="""
      &#128653; <b>%{customdata[0]}
      </b></br></br></br>
      &#128204; %{customdata[1]}</br>
      &#9201; %{customdata[2]}""")

fig.update_traces(visible='legendonly', selector={'name':'bus'})
fig.update_traces(visible='legendonly', selector={'name':'troli'})
fig.update_traces(visible='legendonly', selector={'name':'metro'})
fig.update_traces(visible='legendonly', selector={'name':'HEV'})
fig.show()

# Cell storage
converted to md, so it wont run